In [ ]:
# ***************code description -- Part 1**********************#
# use the multiple APIs in the Python-based wrapper -- pybliometrics 
# to extract the 3-level information for the papers in the provided csv file

# --3 levels of info: 
# --author information (saved in 'Final_author_list.csv'),
# --paper informarion (saved in 'Docu_DOI.csv'),
# --and Plumx information (saved in 'Docu_Plum.csv')

# --APIs: Search API, Retrieval API, Metadata API

# note: pybliometrics  needs to be used within campus network environment

In [130]:
import pybliometrics
import xlsxwriter
# pybliometrics.scopus.utils.create_config()
from pybliometrics.scopus import AffiliationSearch
from pybliometrics.scopus import AuthorSearch
from pybliometrics.scopus import CitationOverview
from pybliometrics.scopus import PlumXMetrics
from pybliometrics.scopus import ScopusSearch
from pybliometrics.scopus import AuthorRetrieval
from pybliometrics.scopus.exception import Scopus429Error, Scopus400Error, Scopus404Error
from pybliometrics.scopus import config
from pybliometrics.scopus import PlumXMetrics
from pybliometrics.scopus import CitationOverview
import pandas as pd
import re
import pandasql as ps

In [131]:
###data cleaning for csv sheet

In [132]:
score_df = pd.read_csv('SCORE.csv')
print(score_df.head(5))
print(len(score_df))

                                            title_CR author_last_CR  \
0  From belief to deceit: How expectancies about ...          Mason   
1  (Pre)occupations: A data-driven model of jobs ...         Imhoff   
2  CEOs imbue organizations with feelings, increa...           Tang   
3  Simultaneous ingroup and outgroup favoritism i...            Axt   
4  Representing other minds: Mental state referen...        McClung   

  author_first_CR  pub_year_CR                      DOI_CR    ISSN_CR  \
0        Malia F.         2018  10.1016/j.jesp.2018.02.013  0022-1031   
1          Roland         2018  10.1016/j.jesp.2018.04.001  0022-1031   
2          Simone         2018  10.1016/j.jesp.2018.06.002  0022-1031   
3       Jordan R.         2018  10.1016/j.jesp.2018.08.007  0022-1031   
4  Jennifer Susan         2018  10.1016/j.jesp.2017.11.013  0022-1031   

                              publication_CR         pub_short  \
0  Journal of Experimental Social Psychology  JournExpSocPsych   
1 

In [133]:
score_df.columns

Index(['title_CR', 'author_last_CR', 'author_first_CR', 'pub_year_CR',
       'DOI_CR', 'ISSN_CR', 'publication_CR', 'pub_short',
       'publication_standard', 'paper_id', 'source_WOS', 'author_full',
       'title_WOS', 'publication_WOS', 'language', 'keywords', 'keywords_plus',
       'abstract', 'author_address', 'reprint_address', 'author_email',
       'funding', 'publisher', 'publisher_address', 'ISSN_WOS', 'eISSN',
       'pub_year_WOS', 'volume', 'issue', 'DOI_WOS', 'WOS_category',
       'category', 'accession_number', 'pg', 'author_last_WOS',
       'author_first_WOS', 'published', 'pdf_filename', 'claim2_abstract',
       'coded_claim2', 'claim2_pg', 'claim2_start', 'claim2_box',
       'claim3a_concretehyp', 'coded_claim3a', 'claim3a_pg', 'claim3a_start',
       'claim3a_box', 'claim3b_testspec', 'coded_claim3b', 'claim3b_pg',
       'claim3b_start', 'claim3b_box', 'claim4_inftest', 'coded_claim4',
       'claim4_pg', 'claim4_start', 'claim4_box', 'sample_size',
       'co

In [134]:
score_df['author_last_CR'] = [str(i).lower() for i in score_df['author_last_CR']] 
score_df['author_first_CR'] = [str(i).lower() for i in score_df['author_first_CR']] 
score_df["author_full_name_CR"] = score_df["author_last_CR"] + " " + score_df["author_first_CR"]
score_df['category'] = [str(i).lower() for i in score_df['category']] 
score_df['publication_standard'] = [str(i).lower() for i in score_df['publication_standard']]
print(score_df.head(5))

                                            title_CR author_last_CR  \
0  From belief to deceit: How expectancies about ...          mason   
1  (Pre)occupations: A data-driven model of jobs ...         imhoff   
2  CEOs imbue organizations with feelings, increa...           tang   
3  Simultaneous ingroup and outgroup favoritism i...            axt   
4  Representing other minds: Mental state referen...        mcclung   

  author_first_CR  pub_year_CR                      DOI_CR    ISSN_CR  \
0        malia f.         2018  10.1016/j.jesp.2018.02.013  0022-1031   
1          roland         2018  10.1016/j.jesp.2018.04.001  0022-1031   
2          simone         2018  10.1016/j.jesp.2018.06.002  0022-1031   
3       jordan r.         2018  10.1016/j.jesp.2018.08.007  0022-1031   
4  jennifer susan         2018  10.1016/j.jesp.2017.11.013  0022-1031   

                              publication_CR         pub_short  \
0  Journal of Experimental Social Psychology  JournExpSocPsych   
1 

In [135]:
###extract affiliation info from author address
# med_list = []
# univ_output = []
# score_df['author_address'] = [str(i).lower() for i in score_df['author_address']] 
# AuthorAddress_list = score_df['author_address'].tolist()
# # AuthorAddress_list = list(set(AuthorAddress_list))
# for addr in AuthorAddress_list:
#     print("------------------------------------------")
#     med_list = re.split(';|\]|\[|,', addr)
#     print(med_list)
#     print("----------------------------------")
#     univ_list = []
#     for univ in med_list:
#         if 'univ' in univ:
# #             print(univ)
#             univ_list.append(univ)
#         elif 'coll' in univ:
# #             print(univ)
#             univ_list.append(univ)
#         else:
#             pass
# #             print("no records!")
#     print(univ_list)
#     if len(univ_list) != 0:
#         univ_value = univ_list[0]
#     else:
#         univ_value = ''
#     print(univ_value)
#     univ_output.append(univ_value)


In [137]:
# univ_output_1 = [x.strip(' ') for x in univ_output]
# print(univ_output_1)
# print(len(univ_output_1))
# univ_df = pd.Series(univ_output_1)
# score_df['author_affiliation'] = univ_df.values

In [138]:
print(score_df.columns)
print(score_df.head(20))

Index(['title_CR', 'author_last_CR', 'author_first_CR', 'pub_year_CR',
       'DOI_CR', 'ISSN_CR', 'publication_CR', 'pub_short',
       'publication_standard', 'paper_id', 'source_WOS', 'author_full',
       'title_WOS', 'publication_WOS', 'language', 'keywords', 'keywords_plus',
       'abstract', 'author_address', 'reprint_address', 'author_email',
       'funding', 'publisher', 'publisher_address', 'ISSN_WOS', 'eISSN',
       'pub_year_WOS', 'volume', 'issue', 'DOI_WOS', 'WOS_category',
       'category', 'accession_number', 'pg', 'author_last_WOS',
       'author_first_WOS', 'published', 'pdf_filename', 'claim2_abstract',
       'coded_claim2', 'claim2_pg', 'claim2_start', 'claim2_box',
       'claim3a_concretehyp', 'coded_claim3a', 'claim3a_pg', 'claim3a_start',
       'claim3a_box', 'claim3b_testspec', 'coded_claim3b', 'claim3b_pg',
       'claim3b_start', 'claim3b_box', 'claim4_inftest', 'coded_claim4',
       'claim4_pg', 'claim4_start', 'claim4_box', 'sample_size',
       'co

In [139]:
###output area category
area_category = score_df['category'].tolist()
area_category = list(set(area_category))
print(len(area_category))
print(area_category)

23
['business & economics; operations research & management science', 'psychology; behavioral sciences; biomedical social sciences', 'government & law', 'family studies; sociology', 'education & educational research; psychology', 'criminology & penology', 'environmental sciences & ecology; psychology', 'public administration', 'business & economics; psychology', 'psychology; business & economics', 'nan', 'government & law; psychology', 'demography', 'psychology; psychiatry', 'education & educational research', 'psychology', 'international relations; government & law', 'development studies; business & economics', 'sociology', 'business & economics; mathematics; mathematical methods in social sciences', 'business & economics', 'education & educational research; rehabilitation', 'government & law; public administration']


In [ ]:
###output 
public_place = score_df['publication_standard'].tolist()
public_place = list(set(public_place))
print(len(public_place))
print(public_place)

In [ ]:
df_category = pd.DataFrame(area_category)
df_public = pd.DataFrame(public_place)
data_category = pd.ExcelWriter('output_sheet.xlsx', engine='xlsxwriter')
df_public.to_excel(data_category,sheet_name='publish',index=False)
df_category.to_excel(data_category,sheet_name='area',index=False)
data_category.save()


In [ ]:
##author level mining

In [ ]:
# ###based on full names
# AuthorFullN_list =score_df["author_full_name_CR"].tolist() 
# print(AuthorFullN_list)

In [ ]:
# author_comp_d0 = []
# for FullN in AuthorFullN_list:
# #     print(LN, ", ", FN)
#     author_str = 'FIRSTAUTH (' + FullN + ')'
#     print(author_str)
#     AuthorInfo = AuthorSearch(author_str, integrity_fields=["eid"], integrity_action="warn", refresh=True,count =200)
#     AuthorInfo_df = pd.DataFrame(AuthorInfo.authors)
#     print(AuthorInfo_df)
# #     try:
# #         AuthorInfo = AuthorSearch(author_str, integrity_fields=["eid"], integrity_action="warn", refresh=True,count =200)
# #         AuthorInfo_df = pd.DataFrame(AuthorInfo.authors)
# #         print(AuthorInfo_df)
# #     except (Scopus429Error, Scopus400Error):
# #         print("escape this author")
# #         continue
# #         AuthorInfo = AuthorSearch(author_str, integrity_fields=["eid"], integrity_action="warn", refresh=True, count =20)
# #         AuthorInfo_df = pd.DataFrame(AuthorInfo.authors)
# #         print(AuthorInfo_df)
#     author_comp_d0.append(AuthorInfo_df)
# author_comp_d0 = pd.concat(author_comp_d)
# # print(author_comp_d0)

In [ ]:
# ##based on first name and last name separately
# AuthorAF_list = score_df['author_affiliation'].tolist()
# AuthorLN_list = score_df['author_last_CR'].tolist()
# AuthorFN_list = score_df['author_first_CR'].tolist()
# AuthorN_tuples = list(zip(AuthorLN_list, AuthorFN_list))
# print("number of authors: ", len(AuthorN_tuples))
# print(AuthorN_tuples)

In [ ]:
# author_comp_d = []
# for LN, FN in AuthorN_tuples:
# #     print(LN, ", ", FN)
#     author_str = 'AUTHLAST(' + LN + ') and AUTHFIRST(' + FN + ')'
#     try:
#         AuthorInfo = AuthorSearch(author_str, integrity_fields=["eid"], integrity_action="warn", count =200)
#         AuthorInfo_df = pd.DataFrame(AuthorInfo.authors)
#         print(AuthorInfo_df)
#     except (Scopus429Error, Scopus400Error):
#         print("escape this author")
#         continue

#     author_comp_d.append(AuthorInfo_df)
#     author_comp_df = pd.concat(author_comp_d)


In [ ]:
# print(author_comp_df.head(10))
# author_comp_df['author_lastn'] = [str(i).lower() for i in author_comp_df['surname']] 
# author_comp_df['author_firstn'] = [str(i).lower() for i in author_comp_df['givenname']] 
# author_comp_df["full_name"] = author_comp_df["author_lastn"] + " " + author_comp_df["author_firstn"]
# ####check how many author are missing
# author_unique = author_comp_df["full_name"].tolist()
# author_unique = list(set(author_unique))


In [ ]:
# ###check author names -- multiple names belongs to one author --this sitaution exists
# print("Unique user names: ", len(author_unique))
# print("-------------------------------------------------------------------")
# author_unique.sort()
# print(author_unique)

In [ ]:
# ###parse EID:
# Author_EID_list = author_comp_df['eid'].tolist()
# Author_EID_list_1 = [x.strip(' ') for x in Author_EID_list]
# eid_list = []
# eid_final_list = []
# for eid_parsed in Author_EID_list_1:
#     print("------------------------------------------")
#     eid_list = re.split('-', eid_parsed)
#     print("eid: ", eid_list[-1])
#     eid_final_list.append(eid_list[-1])

In [ ]:
# ##total number of eids 
# print(len(eid_final_list))

In [ ]:
##get document information in order to target author

In [ ]:
AuthorDOI_list = score_df['DOI_CR'].tolist()
AuthorDOI_list_1 = [str(x).strip(' ') for x in AuthorDOI_list]

In [ ]:
doi_comp_d = []
for DOI in AuthorDOI_list_1:
    DOI_str = 'DOI(' + DOI + ')'
    print(DOI_str)
    DocuInfo = ScopusSearch(DOI_str)
    docu_df = pd.DataFrame(pd.DataFrame(DocuInfo.results))
    print(docu_df)
    doi_comp_d.append(docu_df)
    doi_comp_df = pd.concat(doi_comp_d)

In [ ]:
print(doi_comp_df.head(3))
print("document count: ", len(doi_comp_df))
doi_comp_df.to_csv('Docu_DOI.csv') 

In [126]:
docu_df = pd.read_csv('Docu_DOI.csv')
print("record count: ", len(docu_df))
print(docu_df.head(10))

record count:  2780
   Unnamed: 0  Unnamed: 0.1                 eid                         doi  \
0           0             0  2-s2.0-85042850238  10.1016/j.jesp.2018.02.013   
1           1             0  2-s2.0-85046140774  10.1016/j.jesp.2018.04.001   
2           2             0  2-s2.0-85050101833  10.1016/j.jesp.2018.06.002   
3           3             0  2-s2.0-85052453579  10.1016/j.jesp.2018.08.007   
4           4             0  2-s2.0-85035217499  10.1016/j.jesp.2017.11.013   
5           5             0  2-s2.0-84998881876  10.1016/j.jesp.2016.07.006   
6           6             0  2-s2.0-84992710848  10.1016/j.jesp.2016.08.001   
7           7             0  2-s2.0-85018386088  10.1016/j.jesp.2016.11.014   
8           8             0  2-s2.0-85022082184  10.1016/j.jesp.2017.06.015   
9           9             0  2-s2.0-85028362827  10.1016/j.jesp.2017.07.008   

                 pii  pubmed_id  \
0  S002210311630600X        NaN   
1  S0022103117308533        NaN   
2  S0

In [ ]:
###########get plumx data -- by DOI

In [ ]:
plum_comp_d = []
for DOI in AuthorDOI_list_1:
    try:
        Docu_PlumInfo = PlumXMetrics(DOI, id_type='doi')
    #     print(Docu_PlumInfo)
        plum_capture_df = pd.DataFrame(Docu_PlumInfo.capture).T
#         print(plum_capture_df)

        
        plum_category_totals_df = pd.DataFrame(Docu_PlumInfo.category_totals).T


        
        plum_usage_df = pd.DataFrame(Docu_PlumInfo.usage).T

        
        plum_df = pd.concat([plum_capture_df, plum_category_totals_df, plum_usage_df], axis=1)
        plum_df.columns = range(plum_df.shape[1])
        new_header = plum_df.iloc[0] #grab the first row for the header
        plum_df = plum_df[1:] #take the data less the header row
        plum_df.columns = new_header #set the header row as the df header
        plum_df['doi'] = DOI
        
    except (Scopus429Error, Scopus404Error):
        print("escape this paper")
        continue
    print(plum_df)
    plum_comp_d.append(plum_df)
    plum_comp_df = pd.concat(plum_comp_d)      

In [ ]:
print(plum_comp_df.head(30))
print("document count: ", len(plum_comp_df))
plum_comp_df.to_csv('Docu_Plum.csv') 

In [ ]:
docu_plum_df = pd.read_csv('Docu_Plum.csv')
print("record count: ", len(docu_plum_df))
print(docu_plum_df.head(10))

In [ ]:
###get author information by --EID or DOI

In [6]:
docu_df = pd.read_csv('Docu_DOI.csv')
print("record count: ", len(docu_df))
print(docu_df.head(10))

record count:  2780
   Unnamed: 0                 eid                         doi  \
0           0  2-s2.0-85042850238  10.1016/j.jesp.2018.02.013   
1           0  2-s2.0-85046140774  10.1016/j.jesp.2018.04.001   
2           0  2-s2.0-85050101833  10.1016/j.jesp.2018.06.002   
3           0  2-s2.0-85052453579  10.1016/j.jesp.2018.08.007   
4           0  2-s2.0-85035217499  10.1016/j.jesp.2017.11.013   
5           0  2-s2.0-84998881876  10.1016/j.jesp.2016.07.006   
6           0  2-s2.0-84992710848  10.1016/j.jesp.2016.08.001   
7           0  2-s2.0-85018386088  10.1016/j.jesp.2016.11.014   
8           0  2-s2.0-85022082184  10.1016/j.jesp.2017.06.015   
9           0  2-s2.0-85028362827  10.1016/j.jesp.2017.07.008   

                 pii  pubmed_id  \
0  S002210311630600X        NaN   
1  S0022103117308533        NaN   
2  S0022103117307606        NaN   
3  S0022103118301744        NaN   
4  S0022103117301828        NaN   
5  S0022103116301470        NaN   
6  S002210311630155

In [128]:
##check author name and id matching relationship
# print(docu_df['author_ids'])

In [127]:
# print(docu_df['author_names'])

In [52]:
###parse author_ID:
Author_EID_list = docu_df['author_ids'].tolist()
Author_EID_list_1 = [x.strip(' ') for x in Author_EID_list]
auid_list = []
auid_final_list = []
for auid_parsed in Author_EID_list_1:
    print("------------------------------------------")
    auid_list = re.split(';', auid_parsed)
    print(auid_list)
    print("1stAuthor id: ", auid_list[0])
    print("----------------------------------")
    auid_final_list.append(auid_list[0])
    

------------------------------------------
['35552623800', '55623562400', '7101711997']
1stAuthor id:  35552623800
----------------------------------
------------------------------------------
['35200726200', '49561437500', '57201792247']
1stAuthor id:  35200726200
----------------------------------
------------------------------------------
['56120400200', '15520639300']
1stAuthor id:  56120400200
----------------------------------
------------------------------------------
['56389502300', '55432896900', '15055305000']
1stAuthor id:  56389502300
----------------------------------
------------------------------------------
['56041022100', '55405141800']
1stAuthor id:  56041022100
----------------------------------
------------------------------------------
['25648957400', '57203424384']
1stAuthor id:  25648957400
----------------------------------
------------------------------------------
['55574863500', '37104831400', '23569737700', '15727080800']
1stAuthor id:  55574863500
---------

1stAuthor id:  56102282300
----------------------------------
------------------------------------------
['57199392781', '35322991600']
1stAuthor id:  57199392781
----------------------------------
------------------------------------------
['56625567600', '8585709500']
1stAuthor id:  56625567600
----------------------------------
------------------------------------------
['56912243000', '55645834400']
1stAuthor id:  56912243000
----------------------------------
------------------------------------------
['24822055600', '55654137400', '55538847000', '24331500100', '17636214600']
1stAuthor id:  24822055600
----------------------------------
------------------------------------------
['25228089900', '7401778974', '55915404200', '7103232231', '7005933195', '55027467100']
1stAuthor id:  25228089900
----------------------------------
------------------------------------------
['37261551100', '57205216629', '7201608519', '7006648995']
1stAuthor id:  37261551100
----------------------------

1stAuthor id:  10243468900
----------------------------------
------------------------------------------
['55901124400', '6602134841']
1stAuthor id:  55901124400
----------------------------------
------------------------------------------
['55392847400', '56565973600', '57203018008', '7202716984', '57202193909']
1stAuthor id:  55392847400
----------------------------------
------------------------------------------
['55358508100', '36975176300', '35421629200']
1stAuthor id:  55358508100
----------------------------------
------------------------------------------
['56324335000', '23766778300', '7003774282']
1stAuthor id:  56324335000
----------------------------------
------------------------------------------
['16029356900', '57194698988']
1stAuthor id:  16029356900
----------------------------------
------------------------------------------
['16402299000', '55413598500', '15061117700', '6602855490', '55601365900', '16173985400', '7202615403', '6507058081', '7003284294']
1stAuthor i

----------------------------------
------------------------------------------
['7102044319', '56587368500']
1stAuthor id:  7102044319
----------------------------------
------------------------------------------
['22985107800', '56789756900']
1stAuthor id:  22985107800
----------------------------------
------------------------------------------
['56352574400', '7401521574', '6603414469']
1stAuthor id:  56352574400
----------------------------------
------------------------------------------
['34868091900', '37011501600', '6603617961']
1stAuthor id:  34868091900
----------------------------------
------------------------------------------
['7202649696', '25630694300', '7404701175']
1stAuthor id:  7202649696
----------------------------------
------------------------------------------
['54896688900', '24169803600']
1stAuthor id:  54896688900
----------------------------------
------------------------------------------
['54897607700', '54897806700']
1stAuthor id:  54897607700
-----------

1stAuthor id:  55478137400
----------------------------------
------------------------------------------
['36708130900', '6701621055']
1stAuthor id:  36708130900
----------------------------------
------------------------------------------
['7201876725', '36449251800']
1stAuthor id:  7201876725
----------------------------------
------------------------------------------
['6508204775', '7201717879']
1stAuthor id:  6508204775
----------------------------------
------------------------------------------
['9738184300', '23037784200']
1stAuthor id:  9738184300
----------------------------------
------------------------------------------
['8976700000', '24824916100', '23098924600']
1stAuthor id:  8976700000
----------------------------------
------------------------------------------
['6603458785']
1stAuthor id:  6603458785
----------------------------------
------------------------------------------
['36195543200']
1stAuthor id:  36195543200
----------------------------------
-------------

In [10]:
auid_final_list_1 = []

for x in auid_final_list:
    x = x.strip(' ')
    x = x= int(x)
    auid_final_list_1.append(x)
print(auid_final_list_1[0:10])
print(len(auid_final_list_1))

[35552623800, 35200726200, 56120400200, 56389502300, 56041022100, 25648957400, 55574863500, 56646616100, 57194583822, 18534392600]
2780


In [59]:
docu_df['FirstAuthor_ID'] = auid_final_list_1
print(docu_df.columns)
docu_df.to_csv('Docu_DOI.csv') 
docu_df_1 = pd.read_csv('Docu_DOI.csv')
print("record count: ", len(docu_df_1))
print(docu_df.head(10))

Index(['Unnamed: 0', 'eid', 'doi', 'pii', 'pubmed_id', 'title', 'subtype',
       'subtypeDescription', 'creator', 'afid', 'affilname',
       'affiliation_city', 'affiliation_country', 'author_count',
       'author_names', 'author_ids', 'author_afids', 'coverDate',
       'coverDisplayDate', 'publicationName', 'issn', 'source_id', 'eIssn',
       'aggregationType', 'volume', 'issueIdentifier', 'article_number',
       'pageRange', 'description', 'authkeywords', 'citedby_count',
       'openaccess', 'fund_acr', 'fund_no', 'fund_sponsor', 'FirstAuthor_ID'],
      dtype='object')
record count:  2780
   Unnamed: 0                 eid                         doi  \
0           0  2-s2.0-85042850238  10.1016/j.jesp.2018.02.013   
1           0  2-s2.0-85046140774  10.1016/j.jesp.2018.04.001   
2           0  2-s2.0-85050101833  10.1016/j.jesp.2018.06.002   
3           0  2-s2.0-85052453579  10.1016/j.jesp.2018.08.007   
4           0  2-s2.0-85035217499  10.1016/j.jesp.2017.11.013   
5   

In [95]:
author_comp_d = []
i = 0

_keys = ["a3479b8249e1260478237e00a795334a", "9b985b921628c1d7dc6fc60c626780b5", "f8709a26c38caff8ac1af7a03f5de9ef"]
error = True
while error:
    for auID in auid_final_list_1:
    #     print(auID)
        i = i + 1
        print(i)
        try:
            author_1st_Info = AuthorRetrieval(auID, refresh=True)
            error = False
            
            author_df_p1 = {'author_lastName': author_1st_Info.surname, 'author_firstName': author_1st_Info.given_name, 
                            'uniqueness': author_1st_Info.estimate_uniqueness(),'citation_count': author_1st_Info.citation_count, 
                            'cited_by_count': author_1st_Info.cited_by_count,'h_index': author_1st_Info.h_index, 'document_count': author_1st_Info.document_count}
            author_df_part1 = pd.DataFrame(data = author_df_p1, index = [0])
#             print(author_df_part1)


            currnt_affiliation_info = pd.DataFrame(author_1st_Info.affiliation_current)
            if 'preferred_name' in currnt_affiliation_info.columns:
                currnt_affiliation_df = currnt_affiliation_info[['preferred_name', 'country', 'city', 'org_domain']]
                currnt_affiliation_df.columns = [ 'Current_Affiliation_Name', 'Current_Affiliation_Country', 'Current_Affiliation_City', 'Current_Affiliation_Domain'] 
                author_df_part2 =currnt_affiliation_df
#                 print(author_df_part2)
            else:
                author_df_p2 = {'Current_Affiliation_Name': '', 
                                'Current_Affiliation_Country': '',
                                'Current_Affiliation_City': '', 
                                'Current_Affiliation_Domain': ''}
                author_df_part2 = pd.DataFrame(data = author_df_p2, index = [0])

            history_affiliation_info = pd.DataFrame(author_1st_Info.affiliation_history)
            if 'type' in history_affiliation_info.columns:
                history_affiliation_info = history_affiliation_info.loc[history_affiliation_info['type'] == 'parent']
                history_affiliation_name_list = history_affiliation_info['preferred_name'].tolist()
                history_affiliation_country_list = history_affiliation_info['country'].tolist()
                history_affiliation_city_list = history_affiliation_info['city'].tolist()
                history_affiliation_org_URL_list = history_affiliation_info['org_URL'].tolist()
                history_affiliation_name=';'.join([str(x) for x in history_affiliation_name_list])
                history_affiliation_country=';'.join([str(x) for x in history_affiliation_country_list])
                history_affiliation_city=';'.join([str(x) for x in history_affiliation_city_list])
                history_affiliation_org_URL=';'.join([str(x) for x in history_affiliation_org_URL_list])
                author_df_p3 = {'history_affiliation_name': history_affiliation_name, 
                                'history_affiliation_country': history_affiliation_country,
                                'history_affiliation_city': history_affiliation_city, 
                                'history_affiliation_org_URL': history_affiliation_org_URL}
                author_df_part3 = pd.DataFrame(data = author_df_p3, index = [0])
        #         print(author_df_part3)
            else:
                author_df_p3 = {'history_affiliation_name': '', 
                                'history_affiliation_country': '',
                                'history_affiliation_city': '', 
                                'history_affiliation_org_URL': ''}
                author_df_part3 = pd.DataFrame(data = author_df_p3, index = [0])
                
            history_journal_Info = pd.DataFrame(author_1st_Info.journal_history)
            if 'sourcetitle' in history_journal_Info.columns:
                jounal_history_name_list = history_journal_Info['sourcetitle'].tolist()
                jounal_history_ISSN_list = history_journal_Info['issn'].tolist()
                jounal_history_name =';'.join([str(x) for x in jounal_history_name_list])
                jounal_history_ISSN =';'.join([str(x) for x in jounal_history_ISSN_list])
                author_df_p4 = {'jounal_history_name': jounal_history_name, 
                                'jounal_history_ISSN': jounal_history_ISSN}
                author_df_part4 = pd.DataFrame(data = author_df_p4, index = [0])
                print(author_df_part4) 
            else:
                author_df_p4 = {'jounal_history_name': '', 
                                'jounal_history_ISSN': ''}
                author_df_part4 = pd.DataFrame(data = author_df_p4, index = [0])
                
            

            author_df = pd.concat([author_df_part1, author_df_part2, author_df_part3, author_df_part4], axis=1)
            author_df['author'] = auID
            print(author_df)
        except (Scopus404Error, Scopus400Error):
            print("escape this paper")
            continue
        except Scopus429Error:
            # Remove the last item in _keys to assign it as new API key
             config["Authentication"]["APIKey"] = _keys.pop()
        author_comp_d.append(author_df)
        author_comp_df = pd.concat(author_comp_d)  
    

1
                                 jounal_history_ISSN  \
0  None;0278016X;13684302;10960465;00221031;16183...   

                                 jounal_history_name  
0  The SAGE Handbook of Social Cognition;Social C...  
  author_firstName author_lastName citation_count cited_by_count  \
0         Malia F.           Mason           3232           2928   

  document_count h_index  uniqueness  Current_Affiliation_Name  \
0             40      21           1  Columbia Business School   

  Current_Affiliation_Country Current_Affiliation_City  \
0               United States                 New York   

  Current_Affiliation_Domain          history_affiliation_city  \
0           gsb.columbia.edu  New York;New York;Boston;Hanover   

                         history_affiliation_country  \
0  United States;United States;United States;Unit...   

                            history_affiliation_name  \
0  Columbia Business School;Columbia University i...   

                         hist

                   jounal_history_ISSN  \
0  15298876;00223514;10960465;15527433   

                                 jounal_history_name  
0  Self and Identity;Journal of Personality and S...  
  author_firstName author_lastName citation_count cited_by_count  \
0         Peter V.          Zunick             14             14   

  document_count h_index  uniqueness  Current_Affiliation_Name  \
0              4       2           1  Department of Psychology   

  Current_Affiliation_Country Current_Affiliation_City  \
0               United States               Shreveport   

  Current_Affiliation_Domain history_affiliation_city  \
0              centenary.edu                 Columbus   

  history_affiliation_country   history_affiliation_name  \
0               United States  The Ohio State University   

  history_affiliation_org_URL                  jounal_history_ISSN  \
0        https://www.osu.edu/  15298876;00223514;10960465;15527433   

                                 jounal_h

                    jounal_history_ISSN  \
0  07484526;None;10960465;None;01461672   

                                 jounal_history_name  
0  Negotiation Journal;Academy of Management 2010...  
  author_firstName author_lastName citation_count cited_by_count  \
0       Connson C.           Locke             55             53   

  document_count h_index  uniqueness  \
0              5       4           2   

                           Current_Affiliation_Name  \
0  London School of Economics and Political Science   

  Current_Affiliation_Country Current_Affiliation_City  \
0              United Kingdom                   London   

  Current_Affiliation_Domain history_affiliation_city  \
0                  lse.ac.uk          London;Berkeley   

    history_affiliation_country  \
0  United Kingdom;United States   

                            history_affiliation_name  \
0  London School of Economics and Political Scien...   

                       history_affiliation_org_URL  \
0  h

                                 jounal_history_ISSN  \
0  10990720;15327582;19326203;10960465;13620436;1...   

                                 jounal_history_name  
0  Applied Cognitive Psychology;International Jou...  
  author_firstName author_lastName citation_count cited_by_count  \
0       Jan Willem    van Prooijen           1649           1159   
1              NaN             NaN            NaN            NaN   

  document_count h_index  uniqueness Current_Affiliation_Name  \
0             83      22         1.0                       VU   
1            NaN     NaN         NaN                     NSCR   

  Current_Affiliation_Country Current_Affiliation_City  \
0                 Netherlands                     None   
1                 Netherlands                Amsterdam   

  Current_Affiliation_Domain  \
0                       None   
1                       None   

                            history_affiliation_city  \
0  Amsterdam;None;Amsterdam;Leiden;Amsterdam;Ams

                                 jounal_history_ISSN  \
0  19311516;02782626;17470919;0278016X;10964657;1...   

                                 jounal_history_name  
0  Emotion;Brain and Cognition;Social Neuroscienc...  
  author_firstName author_lastName citation_count cited_by_count  \
0        Robert G.        Franklin            686            601   

  document_count h_index  uniqueness           Current_Affiliation_Name  \
0             27      14           1  Department of Behavioral Sciences   

  Current_Affiliation_Country Current_Affiliation_City  \
0               United States                 Anderson   

  Current_Affiliation_Domain history_affiliation_city  \
0                     ac.edu  Waltham;University Park   

   history_affiliation_country  \
0  United States;United States   

                            history_affiliation_name  \
0  Brandeis University;Pennsylvania State University   

                    history_affiliation_org_URL  \
0  http://www.brandeis.e

...

2753
                                 jounal_history_ISSN  \
0  01432095;1537260X;None;10477039;20411723;14679...   

                                 jounal_history_name  
0  Strategic Management Journal;Academy of Manage...  
  author_firstName author_lastName citation_count cited_by_count  \
0          Adam M.       Kleinbaum            470            414   

  document_count h_index  uniqueness              Current_Affiliation_Name  \
0             18      10           1  Tuck School of Business at Dartmouth   

  Current_Affiliation_Country Current_Affiliation_City  \
0               United States                  Hanover   

  Current_Affiliation_Domain          history_affiliation_city  \
0         tuck.dartmouth.edu  Hanover;Hanover;Boston;Cambridge   

                         history_affiliation_country  \
0  United States;United States;United States;Unit...   

                            history_affiliation_name  \
0  Tuck School of Business at Dartmouth;Dartmouth...   

  

2760
                                 jounal_history_ISSN  \
0  03623319;0049089X;09234748;13540688;23306696;1...   

                                 jounal_history_name  
0  Social Science Journal;Social Science Research...  
  author_firstName author_lastName citation_count cited_by_count  \
0    David Matthew      Waguespack            724            702   

  document_count h_index  uniqueness               Current_Affiliation_Name  \
0             14       9           1  Department of Government and Politics   

  Current_Affiliation_Country Current_Affiliation_City  \
0               United States             College Park   

  Current_Affiliation_Domain   history_affiliation_city  \
0                    umd.edu  College Park;College Park   

   history_affiliation_country  \
0  United States;United States   

                            history_affiliation_name  \
0  Robert H. Smith School of Business;University ...   

                     history_affiliation_org_URL  \
0  htt

2767
                                 jounal_history_ISSN  \
0  15566501;None;None;None;07475632;22111670;2211...   

                                 jounal_history_name  
0  Educational Technology Research and Developmen...  
  author_firstName author_lastName citation_count cited_by_count  \
0        Andrew A.          Tawfik            202            159   

  document_count h_index  uniqueness  \
0             36       8           2   

                            Current_Affiliation_Name  \
0  Department of Instructional Design and Technology   

  Current_Affiliation_Country Current_Affiliation_City  \
0               United States                  Memphis   

  Current_Affiliation_Domain                         history_affiliation_city  \
0                memphis.edu  Memphis;DeKalb;Cincinnati;River Forest;Columbia   

                         history_affiliation_country  \
0  United States;United States;United States;Unit...   

                            history_affiliation_

2774
  jounal_history_ISSN                  jounal_history_name
0   18735347;10959203  Social Science and Medicine;Science
  author_firstName author_lastName citation_count cited_by_count  \
0            Carla        Prentice            267            267   

  document_count h_index  uniqueness   Current_Affiliation_Name  \
0              2       2           1  Queen's Management School   

  Current_Affiliation_Country Current_Affiliation_City  \
0              United Kingdom                  Belfast   

  Current_Affiliation_Domain history_affiliation_city  \
0                  qub.ac.uk                            

  history_affiliation_country history_affiliation_name  \
0                                                        

  history_affiliation_org_URL jounal_history_ISSN  \
0                               18735347;10959203   

                   jounal_history_name      author  
0  Social Science and Medicine;Science  8941513200  
2775
                                 jouna

2780
                                 jounal_history_ISSN  \
0  15327795;10902139;14640600;15733297;18392628;1...   

                                 jounal_history_name  
0  Journal of Research on Adolescence;Brain, Beha...  
  author_firstName author_lastName citation_count cited_by_count  \
0        Mollie N.           Moore             69             64   

  document_count h_index  uniqueness         Current_Affiliation_Name  \
0              8       5           1  University of Wisconsin-Madison   

  Current_Affiliation_Country Current_Affiliation_City  \
0               United States                  Madison   

  Current_Affiliation_Domain history_affiliation_city  \
0                   wisc.edu          Madison;Madison   

   history_affiliation_country  \
0  United States;United States   

                         history_affiliation_name  \
0  University of Wisconsin-Madison;Waisman Center   

                        history_affiliation_org_URL  \
0  http://www.wisc.edu;ht

In [96]:
print(author_comp_df.head(2))
print("author count: ", len(author_comp_df))
author_comp_df.to_csv('Docu_anthor.csv') 

  Current_Affiliation_City Current_Affiliation_Country  \
0                 New York               United States   
0                    Mainz                     Germany   

  Current_Affiliation_Domain  Current_Affiliation_Name       author  \
0           gsb.columbia.edu  Columbia Business School  35552623800   
0               uni-mainz.de  Department of Psychology  35200726200   

  author_firstName author_lastName citation_count cited_by_count  \
0         Malia F.           Mason           3232           2928   
0           Roland          Imhoff           1068            866   

  document_count h_index          history_affiliation_city  \
0             40      21  New York;New York;Boston;Hanover   
0             58      19                   Mainz;Koln;Bonn   

                         history_affiliation_country  \
0  United States;United States;United States;Unit...   
0                            Germany;Germany;Germany   

                            history_affiliation_na

In [120]:
author_df = pd.read_csv('Docu_anthor.csv')
print("record count: ", len(author_df))
print(author_df.head(10))

record count:  3001
   Unnamed: 0 Current_Affiliation_City Current_Affiliation_Country  \
0           0                 New York               United States   
1           0                    Mainz                     Germany   
2           0                   Ithaca               United States   
3           0                 Montreal                      Canada   
4           0                Neuchatel                 Switzerland   
5           0                   Newark               United States   
6           0                Cambridge               United States   
7           0               Shreveport               United States   
8           0                   Athens               United States   
9           0                    Tempe               United States   

  Current_Affiliation_Domain                Current_Affiliation_Name  \
0           gsb.columbia.edu                Columbia Business School   
1               uni-mainz.de                Department of Psychol

In [98]:
# print(author_comp_df.columns)
au_record_count= author_df.groupby(['author'], sort=False).size().reset_index(name='au_cnt')
# print(au_record_count)

In [99]:
author_freq_df = pd.merge(author_df, au_record_count, on='author', how='inner')

In [100]:
print(len(author_freq_df))
print(author_freq_df.columns)
print(author_freq_df.head(5))

3001
Index(['Current_Affiliation_City', 'Current_Affiliation_Country',
       'Current_Affiliation_Domain', 'Current_Affiliation_Name', 'author',
       'author_firstName', 'author_lastName', 'citation_count',
       'cited_by_count', 'document_count', 'h_index',
       'history_affiliation_city', 'history_affiliation_country',
       'history_affiliation_name', 'history_affiliation_org_URL',
       'jounal_history_ISSN', 'jounal_history_name', 'uniqueness', 'au_cnt'],
      dtype='object')
  Current_Affiliation_City Current_Affiliation_Country  \
0                 New York               United States   
1                 New York               United States   
2                    Mainz                     Germany   
3                    Mainz                     Germany   
4                   Ithaca               United States   

  Current_Affiliation_Domain                Current_Affiliation_Name  \
0           gsb.columbia.edu                Columbia Business School   
1          

In [102]:
is_unique =  author_freq_df['au_cnt']== 1
is_duplicate =  author_freq_df['au_cnt'] > 1

author_uniqueness_df = author_freq_df[is_unique]
author_duplicate_df = author_freq_df[is_duplicate]

# print(author_uniqueness_df.head(5))
# print(len(author_uniqueness_df))
print(author_duplicate_df.head(5))
print(len(author_duplicate_df))

   Current_Affiliation_City Current_Affiliation_Country  \
0                  New York               United States   
1                  New York               United States   
2                     Mainz                     Germany   
3                     Mainz                     Germany   
12                 Enschede                 Netherlands   

   Current_Affiliation_Domain  Current_Affiliation_Name       author  \
0            gsb.columbia.edu  Columbia Business School  35552623800   
1            gsb.columbia.edu  Columbia Business School  35552623800   
2                uni-mainz.de  Department of Psychology  35200726200   
3                uni-mainz.de  Department of Psychology  35200726200   
12                 utwente.nl      University of Twente  54883551600   

   author_firstName author_lastName citation_count cited_by_count  \
0          Malia F.           Mason           3232           2928   
1          Malia F.           Mason           3232           2928   
2    

In [103]:
author_duplicate_removed = author_duplicate_df.drop_duplicates()
print(author_duplicate_removed)

     Current_Affiliation_City Current_Affiliation_Country  \
0                    New York               United States   
2                       Mainz                     Germany   
12                   Enschede                 Netherlands   
13                    Utrecht                 Netherlands   
16       Saint Martin d'Heres                      France   
26                       None                 Netherlands   
27                  Amsterdam                 Netherlands   
33                   Anderson               United States   
38                    Hanover               United States   
48                      Davis               United States   
49                      Davis               United States   
71                 Stillwater               United States   
72                      Seoul                 South Korea   
73                   Columbia               United States   
75                    Chicago               United States   
77                   Eva

In [115]:
# print(author_duplicate_removed.columns)
q1 = """SELECT * FROM author_duplicate_removed 
                 WHERE author_firstName is not null and author_lastName is not null"""

author_duplicate_removed_1 = ps.sqldf(q1, locals())
print(author_duplicate_removed_1)

    Current_Affiliation_City Current_Affiliation_Country  \
0                   New York               United States   
1                      Mainz                     Germany   
2                   Enschede                 Netherlands   
3       Saint Martin d'Heres                      France   
4                       None                 Netherlands   
5                   Anderson               United States   
6                    Hanover               United States   
7                      Davis               United States   
8                 Stillwater               United States   
9                   Columbia               United States   
10                   Chicago               United States   
11                  Evanston               United States   
12              Coral Gables               United States   
13               Gainesville               United States   
14                  Kutztown               United States   
15                    Irvine            

In [118]:
###
# 7102382566; 55343807000;35363464200 

author_id =  author_duplicate_removed_1['author']== 7102382566
print(author_duplicate_removed_1[author_id])

    Current_Affiliation_City Current_Affiliation_Country  \
321                   Durham               United States   

    Current_Affiliation_Domain                   Current_Affiliation_Name  \
321                   duke.edu  Department of Psychology and Neuroscience   

         author author_firstName author_lastName citation_count  \
321  7102382566         Avshalom           Caspi          68899   

    cited_by_count document_count h_index  \
321          48149            356     141   

                              history_affiliation_city  \
321  London;Durham;London;Chapel Hill;London;Munich...   

                           history_affiliation_country  \
321  United Kingdom;United States;United Kingdom;Un...   

                              history_affiliation_name  \
321  King's College London;Duke University;Medical ...   

                           history_affiliation_org_URL  \
321  http://www.kcl.ac.uk/;https://duke.edu/;http:/...   

                              

In [119]:
author_reunion_df = pd.concat([author_uniqueness_df, author_duplicate_removed_1], axis=0)
print(author_reunion_df.head(5))
print(len(author_reunion_df))


  Current_Affiliation_City Current_Affiliation_Country  \
4                   Ithaca               United States   
5                 Montreal                      Canada   
6                Neuchatel                 Switzerland   
7                   Newark               United States   
8                Cambridge               United States   

  Current_Affiliation_Domain                Current_Affiliation_Name  \
4        johnson.cornell.edu  Cornell SC Johnson College of Business   
5                  mcgill.ca                       McGill University   
6                   unine.ch                Cognitive Science Centre   
7             newark.osu.edu                Department of Psychology   
8                harvard.edu                      Harvard University   

        author author_firstName author_lastName citation_count cited_by_count  \
4  56120400200           Simone            Tang             55             53   
5  56389502300        Jordan R.             Axt         

In [123]:
##check if still duplicated authors
author_reunion_df_check = author_reunion_df.drop('au_cnt' , axis='columns')
auReunion_record_count= author_reunion_df_check.groupby(['author'], sort=False).size().reset_index(name='au_cnt')
# print(auReunion_record_count)
# return 0 records means n duplicated author ID are founded
author_freq =  auReunion_record_count['au_cnt'] > 1
print(auReunion_record_count[author_freq])

Empty DataFrame
Columns: [author, au_cnt]
Index: []


In [129]:
# print(author_reunion_df_check.columns)
author_reunion_df_check.to_csv('Final_author_list.csv') 

In [68]:
###check duplicate recordd
print(author_comp_df.columns)
author_comp_df.sort_values("author", inplace = True)
bool_series = author_comp_df["author"].duplicated() 
author_comp_df.head()
duplicated_df =author_comp_df[bool_series]
print(len(duplicated_df))


Index(['Current_Affiliation_City', 'Current_Affiliation_Country',
       'Current_Affiliation_Domain', 'Current_Affiliation_Name', 'author',
       'citation_count', 'cited_by_count', 'document_count', 'h_index',
       'history_affiliation_city', 'history_affiliation_country',
       'history_affiliation_name', 'history_affiliation_org_URL',
       'jounal_history_ISSN', 'jounal_history_name', 'uniqueness'],
      dtype='object')
389


In [73]:
print(duplicated_df.head(20))
duplicated_df.to_csv('anthor_duplicated.csv') 

  Current_Affiliation_City Current_Affiliation_Country  \
0                   Trento                       Italy   
1               Providence               United States   
0                Vancouver                      Canada   
1               Piscataway               United States   
1                    Davis               United States   
1                   Manama                     Bahrain   
2                  Fairfax               United States   
0                   Trento                       Italy   
0                 Columbus               United States   
0                 Columbus               United States   
1                Cambridge               United States   
0                       As                      Norway   
1                  Bologna                       Italy   
0               Zurich ZH,                 Switzerland   
0                Cambridge               United States   
1                Cambridge               United States   
0             

In [48]:
# type("35552623800")
# author = AuthorRetrieval(35552623800, refresh = True)
# # author.h_index
# # author.affiliation_current
# # author.journal_history
# author.estimate_uniqueness()

1

In [41]:
# history_journal_Info = pd.DataFrame(author.journal_history)
# # print(history_journal_Info)
# jounal_history_name_list = history_journal_Info['sourcetitle'].tolist()
# jounal_history_ISSN_list = history_journal_Info['issn'].tolist()
# jounal_history_name =';'.join([str(x) for x in jounal_history_name_list])
# jounal_history_ISSN =';'.join([str(x) for x in jounal_history_ISSN_list])
# author_df_p4 = {'jounal_history_name': jounal_history_name, 
#                 'jounal_history_ISSN': jounal_history_ISSN}
# author_df_part4 = pd.DataFrame(data = author_df_p4, index = [0])
# print(author_df_part4)

                                 jounal_history_ISSN  \
0  None;0278016X;13684302;10960465;00221031;16183...   

                                 jounal_history_name  
0  The SAGE Handbook of Social Cognition;Social C...  


In [ ]:
# print(author)

In [ ]:
# currnt_affiliation_info = pd.DataFrame(author.affiliation_current)
# currnt_affiliation_df = currnt_affiliation_info[['preferred_name', 'country', 'city', 'org_domain']]
# currnt_affiliation_df.columns = [ 'Current_Affiliation_Name', 'Current_Affiliation_Country', 'Current_Affiliation_City', 'Current_Affiliation_Domain'] 
# author_df_part2 =currnt_affiliation_df
# print(author_df_part2)

In [ ]:
# history_afiiliation_info = pd.DataFrame(author.affiliation_history)
# history_afiiliation_info = history_afiiliation_info.loc[history_afiiliation_info['type'] == 'parent']
# # print(history_afiiliation_info)

# history_afiiliation_name_list = history_afiiliation_info['preferred_name'].tolist()
# history_afiiliation_country_list = history_afiiliation_info['country'].tolist()
# history_afiiliation_city_list = history_afiiliation_info['city'].tolist()
# history_afiiliation_org_URL_list = history_afiiliation_info['org_URL'].tolist()


# history_afiiliation_name =';'.join(history_afiiliation_name_list)
# history_afiiliation_country=';'.join(history_afiiliation_country_list)
# history_afiiliation_city=';'.join(history_afiiliation_city_list)
# # history_afiiliation_org_URL=';'.join(history_afiiliation_org_URL_list)
# history_afiiliation_org_URL = ';'.join([str(x) for x in history_afiiliation_org_URL_list])
# author_df_p3 = {'history_afiiliation_name': history_afiiliation_name, 
#                 'history_afiiliation_country': history_afiiliation_country,
#                 'history_afiiliation_city': history_afiiliation_city, 
#                 'history_afiiliation_org_URL': history_afiiliation_org_URL}
# author_df_part3 = pd.DataFrame(data = author_df_p3, index = [0])
# print(author_df_part3)

In [ ]:
# ##validate plum metrics
# plum = PlumXMetrics("10.1016/j.jesp.2018.04.001", id_type='doi')
# print(plum.capture)
# print(plum.category_totals)
# print(plum.usage)

In [ ]:
# ##get citation information 
# AuthorEID_list = docu_df['eid'].tolist()
# AuthorEID_list_1 = [str(x).strip(' ') for x in AuthorEID_list]

In [ ]:
# co = CitationOverview("2-s2.0-85046140774", start =2000, end = 2020)

In [ ]:
# print(co.cc)

In [ ]:
# print(co.h_index)

In [ ]:
# s = ScopusSearch('DOI(10.1016/j.jesp.2018.02.013)')
# print(s)
# df = pd.DataFrame(pd.DataFrame(s.results))
# print(df)

In [ ]:
# # AuthorInfo = AuthorSearch('AUTHLAST(zhang) and AUTHFIRST(ying)',count=100)
# AuthorInfo = AuthorSearch('AUTHLAST(mason) and AUTHFIRST(malia f.)',count=100)
# print(type(AuthorInfo))
# print(type(AuthorInfo.authors))
# print(pd.DataFrame(AuthorInfo.authors))

In [ ]:
# s = AuthorSearch('AUTHLAST(mason) and AUTHFIRST(malia f.)', integrity_fields=["eid"], integrity_action="warn")
# print(pd.DataFrame(s.authors))

In [ ]:
# au_mm = AuthorRetrieval(56941505900)
# # au_mm = AuthorRetrieval(36992459300)

# print(au_mm)

In [ ]:
# au_mm.citation_count

In [ ]:
# au_mm.document_count

In [ ]:
# au_mm.h_index

In [ ]:
####author's publications
# docu_ids = pd.DataFrame(au_mm.get_documents(refresh=False))

In [ ]:
# docu_ids.shape
# print(docu_ids.columns)
# print(docu_ids)

In [ ]:
# docu_example = ScopusSearch('DOI(10.1016/j.jesp.2018.02.013)')
# print(docu_example)
# docu_example_df = pd.DataFrame(pd.DataFrame(docu_example.results))
# docu_example_df